In [1]:
from IPython.display import display, clear_output
import matplotlib.pyplot as plt
from bs4 import BeautifulSoup
from datetime import datetime
import pandas as pd
import numpy as np
import requests
import warnings
import talib
import json
import time

pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)
warnings.filterwarnings("ignore")

In [2]:
plt.rcParams['figure.figsize'] = (20,10)

In [3]:
patternList = [talib.CDL2CROWS, talib.CDL3BLACKCROWS, talib.CDL3INSIDE, talib.CDL3LINESTRIKE, talib.CDL3OUTSIDE, talib.CDL3STARSINSOUTH, talib.CDL3WHITESOLDIERS, talib.CDLABANDONEDBABY, talib.CDLADVANCEBLOCK, talib.CDLBELTHOLD, talib.CDLBREAKAWAY, talib.CDLCLOSINGMARUBOZU, talib.CDLCONCEALBABYSWALL, talib.CDLCOUNTERATTACK, talib.CDLDARKCLOUDCOVER, talib.CDLDOJI, talib.CDLDOJISTAR, talib.CDLDRAGONFLYDOJI, talib.CDLENGULFING, talib.CDLEVENINGDOJISTAR, talib.CDLEVENINGSTAR, talib.CDLGAPSIDESIDEWHITE, talib.CDLGRAVESTONEDOJI, talib.CDLHAMMER, talib.CDLHANGINGMAN, talib.CDLHARAMI, talib.CDLHARAMICROSS, talib.CDLHIGHWAVE, talib.CDLHIKKAKE, talib.CDLHIKKAKEMOD, talib.CDLHOMINGPIGEON, talib.CDLIDENTICAL3CROWS, talib.CDLINNECK, talib.CDLINVERTEDHAMMER, talib.CDLKICKING, talib.CDLKICKINGBYLENGTH, talib.CDLLADDERBOTTOM, talib.CDLLONGLEGGEDDOJI, talib.CDLLONGLINE, talib.CDLMARUBOZU, talib.CDLMATCHINGLOW, talib.CDLMATHOLD, talib.CDLMORNINGDOJISTAR, talib.CDLMORNINGSTAR, talib.CDLONNECK, talib.CDLPIERCING, talib.CDLRICKSHAWMAN, talib.CDLRISEFALL3METHODS, talib.CDLSEPARATINGLINES, talib.CDLSHOOTINGSTAR, talib.CDLSHORTLINE, talib.CDLSPINNINGTOP, talib.CDLSTALLEDPATTERN, talib.CDLSTICKSANDWICH, talib.CDLTAKURI, talib.CDLTASUKIGAP, talib.CDLTHRUSTING, talib.CDLTRISTAR, talib.CDLUNIQUE3RIVER, talib.CDLUPSIDEGAP2CROWS, talib.CDLXSIDEGAP3METHODS]

In [4]:
dictOfPatterns = {i: list() for i in patternList}

In [5]:
header = {
          "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:92.0) Gecko/20100101 Firefox/92.0",
          "X-Requested-With": "XMLHttpRequest"
        }

In [6]:
wilshire5000TickerList = list(pd.read_csv('wilshire5000.csv')['Ticker'])

In [7]:
%%time
totalNoOfDays = 0
for ticker in wilshire5000TickerList:
    try:
        currentSymbol = ticker
        period1 = int(time.time() - 1633974477) #eternity
        period2 = int(time.time())
        url = f'https://query2.finance.yahoo.com/v8/finance/chart/{currentSymbol}?formatted=true&crumb=LqSYCwMewDq&lang=en-US&region=US&includeAdjustedClose=true&interval=1d&period1={period1}&period2={period2}&events=capitalGain|div|split&useYfid=true&corsDomain=finance.yahoo.com'
        r = requests.get(url, headers=header)
        soup = json.loads(str(BeautifulSoup(r.text, 'html.parser')))

        timestamp = soup['chart']['result'][0]['timestamp']
        openList = soup['chart']['result'][0]['indicators']['quote'][0]['open']
        highList = soup['chart']['result'][0]['indicators']['quote'][0]['high']
        lowList = soup['chart']['result'][0]['indicators']['quote'][0]['low']
        closeList = soup['chart']['result'][0]['indicators']['quote'][0]['close']

        timestamp = [i for i in timestamp if i != None]
        openList = [i for i in openList if i != None]
        highList = [i for i in highList if i != None]
        lowList = [i for i in lowList if i != None]
        closeList = [i for i in closeList if i != None]

        dataframe = pd.DataFrame(list(zip(timestamp, openList, highList, lowList, closeList)), columns=['timestamp', 'open', 'high', 'low', 'close'])
        totalNoOfDays = totalNoOfDays + len(dataframe)

        for pattern in patternList:
            dataframe['pattern'] = pattern(dataframe.open, dataframe.high, dataframe.low, dataframe.close)
            dataframe['shiftedReturn'] = np.log(dataframe['close'].shift(-1)/dataframe['close'])*100
            dataframe['realizedReturn'] = np.where(dataframe['pattern'] == -100, dataframe['shiftedReturn']*-1, dataframe['shiftedReturn'])
            dataframe.dropna(inplace=True)
            print(str(pattern)[10:-23],'for',ticker)
            dictOfPatterns[pattern] = dictOfPatterns[pattern] + list(dataframe[dataframe['pattern'] == -100]['realizedReturn'])
    except:
        pass

CDL2CROWS for A
CDL3BLACKCROWS for A
CDL3INSIDE for A
CDL3LINESTRIKE for A
CDL3OUTSIDE for A
CDL3STARSINSOUTH for A
CDL3WHITESOLDIERS for A
CDLABANDONEDBABY for A
CDLADVANCEBLOCK for A
CDLBELTHOLD for A
CDLBREAKAWAY for A
CDLCLOSINGMARUBOZU for A
CDLCONCEALBABYSWALL for A
CDLCOUNTERATTACK for A
CDLDARKCLOUDCOVER for A
CDLDOJI for A
CDLDOJISTAR for A
CDLDRAGONFLYDOJI for A
CDLENGULFING for A
CDLEVENINGDOJISTAR for A
CDLEVENINGSTAR for A
CDLGAPSIDESIDEWHITE for A
CDLGRAVESTONEDOJI for A
CDLHAMMER for A
CDLHANGINGMAN for A
CDLHARAMI for A
CDLHARAMICROSS for A
CDLHIGHWAVE for A
CDLHIKKAKE for A
CDLHIKKAKEMOD for A
CDLHOMINGPIGEON for A
CDLIDENTICAL3CROWS for A
CDLINNECK for A
CDLINVERTEDHAMMER for A
CDLKICKING for A
CDLKICKINGBYLENGTH for A
CDLLADDERBOTTOM for A
CDLLONGLEGGEDDOJI for A
CDLLONGLINE for A
CDLMARUBOZU for A
CDLMATCHINGLOW for A
CDLMATHOLD for A
CDLMORNINGDOJISTAR for A
CDLMORNINGSTAR for A
CDLONNECK for A
CDLPIERCING for A
CDLRICKSHAWMAN for A
CDLRISEFALL3METHODS for A
CDLSEP

CDL2CROWS for AAON
CDL3BLACKCROWS for AAON
CDL3INSIDE for AAON
CDL3LINESTRIKE for AAON
CDL3OUTSIDE for AAON
CDL3STARSINSOUTH for AAON
CDL3WHITESOLDIERS for AAON
CDLABANDONEDBABY for AAON
CDLADVANCEBLOCK for AAON
CDLBELTHOLD for AAON
CDLBREAKAWAY for AAON
CDLCLOSINGMARUBOZU for AAON
CDLCONCEALBABYSWALL for AAON
CDLCOUNTERATTACK for AAON
CDLDARKCLOUDCOVER for AAON
CDLDOJI for AAON
CDLDOJISTAR for AAON
CDLDRAGONFLYDOJI for AAON
CDLENGULFING for AAON
CDLEVENINGDOJISTAR for AAON
CDLEVENINGSTAR for AAON
CDLGAPSIDESIDEWHITE for AAON
CDLGRAVESTONEDOJI for AAON
CDLHAMMER for AAON
CDLHANGINGMAN for AAON
CDLHARAMI for AAON
CDLHARAMICROSS for AAON
CDLHIGHWAVE for AAON
CDLHIKKAKE for AAON
CDLHIKKAKEMOD for AAON
CDLHOMINGPIGEON for AAON
CDLIDENTICAL3CROWS for AAON
CDLINNECK for AAON
CDLINVERTEDHAMMER for AAON
CDLKICKING for AAON
CDLKICKINGBYLENGTH for AAON
CDLLADDERBOTTOM for AAON
CDLLONGLEGGEDDOJI for AAON
CDLLONGLINE for AAON
CDLMARUBOZU for AAON
CDLMATCHINGLOW for AAON
CDLMATHOLD for AAON
CDLMORN

CDLSTALLEDPATTERN for ABBV
CDLSTICKSANDWICH for ABBV
CDLTAKURI for ABBV
CDLTASUKIGAP for ABBV
CDLTHRUSTING for ABBV
CDLTRISTAR for ABBV
CDLUNIQUE3RIVER for ABBV
CDLUPSIDEGAP2CROWS for ABBV
CDLXSIDEGAP3METHODS for ABBV
CDL2CROWS for ABC
CDL3BLACKCROWS for ABC
CDL3INSIDE for ABC
CDL3LINESTRIKE for ABC
CDL3OUTSIDE for ABC
CDL3STARSINSOUTH for ABC
CDL3WHITESOLDIERS for ABC
CDLABANDONEDBABY for ABC
CDLADVANCEBLOCK for ABC
CDLBELTHOLD for ABC
CDLBREAKAWAY for ABC
CDLCLOSINGMARUBOZU for ABC
CDLCONCEALBABYSWALL for ABC
CDLCOUNTERATTACK for ABC
CDLDARKCLOUDCOVER for ABC
CDLDOJI for ABC
CDLDOJISTAR for ABC
CDLDRAGONFLYDOJI for ABC
CDLENGULFING for ABC
CDLEVENINGDOJISTAR for ABC
CDLEVENINGSTAR for ABC
CDLGAPSIDESIDEWHITE for ABC
CDLGRAVESTONEDOJI for ABC
CDLHAMMER for ABC
CDLHANGINGMAN for ABC
CDLHARAMI for ABC
CDLHARAMICROSS for ABC
CDLHIGHWAVE for ABC
CDLHIKKAKE for ABC
CDLHIKKAKEMOD for ABC
CDLHOMINGPIGEON for ABC
CDLIDENTICAL3CROWS for ABC
CDLINNECK for ABC
CDLINVERTEDHAMMER for ABC
CDLKICKIN

CDLMORNINGDOJISTAR for ABM
CDLMORNINGSTAR for ABM
CDLONNECK for ABM
CDLPIERCING for ABM
CDLRICKSHAWMAN for ABM
CDLRISEFALL3METHODS for ABM
CDLSEPARATINGLINES for ABM
CDLSHOOTINGSTAR for ABM
CDLSHORTLINE for ABM
CDLSPINNINGTOP for ABM
CDLSTALLEDPATTERN for ABM
CDLSTICKSANDWICH for ABM
CDLTAKURI for ABM
CDLTASUKIGAP for ABM
CDLTHRUSTING for ABM
CDLTRISTAR for ABM
CDLUNIQUE3RIVER for ABM
CDLUPSIDEGAP2CROWS for ABM
CDLXSIDEGAP3METHODS for ABM
CDL2CROWS for ABMD
CDL3BLACKCROWS for ABMD
CDL3INSIDE for ABMD
CDL3LINESTRIKE for ABMD
CDL3OUTSIDE for ABMD
CDL3STARSINSOUTH for ABMD
CDL3WHITESOLDIERS for ABMD
CDLABANDONEDBABY for ABMD
CDLADVANCEBLOCK for ABMD
CDLBELTHOLD for ABMD
CDLBREAKAWAY for ABMD
CDLCLOSINGMARUBOZU for ABMD
CDLCONCEALBABYSWALL for ABMD
CDLCOUNTERATTACK for ABMD
CDLDARKCLOUDCOVER for ABMD
CDLDOJI for ABMD
CDLDOJISTAR for ABMD
CDLDRAGONFLYDOJI for ABMD
CDLENGULFING for ABMD
CDLEVENINGDOJISTAR for ABMD
CDLEVENINGSTAR for ABMD
CDLGAPSIDESIDEWHITE for ABMD
CDLGRAVESTONEDOJI for ABM

CDLIDENTICAL3CROWS for ACA
CDLINNECK for ACA
CDLINVERTEDHAMMER for ACA
CDLKICKING for ACA
CDLKICKINGBYLENGTH for ACA
CDLLADDERBOTTOM for ACA
CDLLONGLEGGEDDOJI for ACA
CDLLONGLINE for ACA
CDLMARUBOZU for ACA
CDLMATCHINGLOW for ACA
CDLMATHOLD for ACA
CDLMORNINGDOJISTAR for ACA
CDLMORNINGSTAR for ACA
CDLONNECK for ACA
CDLPIERCING for ACA
CDLRICKSHAWMAN for ACA
CDLRISEFALL3METHODS for ACA
CDLSEPARATINGLINES for ACA
CDLSHOOTINGSTAR for ACA
CDLSHORTLINE for ACA
CDLSPINNINGTOP for ACA
CDLSTALLEDPATTERN for ACA
CDLSTICKSANDWICH for ACA
CDLTAKURI for ACA
CDLTASUKIGAP for ACA
CDLTHRUSTING for ACA
CDLTRISTAR for ACA
CDLUNIQUE3RIVER for ACA
CDLUPSIDEGAP2CROWS for ACA
CDLXSIDEGAP3METHODS for ACA
CDL2CROWS for ACAD
CDL3BLACKCROWS for ACAD
CDL3INSIDE for ACAD
CDL3LINESTRIKE for ACAD
CDL3OUTSIDE for ACAD
CDL3STARSINSOUTH for ACAD
CDL3WHITESOLDIERS for ACAD
CDLABANDONEDBABY for ACAD
CDLADVANCEBLOCK for ACAD
CDLBELTHOLD for ACAD
CDLBREAKAWAY for ACAD
CDLCLOSINGMARUBOZU for ACAD
CDLCONCEALBABYSWALL for A

...

CDL2CROWS for YELP
CDL3BLACKCROWS for YELP
CDL3INSIDE for YELP
CDL3LINESTRIKE for YELP
CDL3OUTSIDE for YELP
CDL3STARSINSOUTH for YELP
CDL3WHITESOLDIERS for YELP
CDLABANDONEDBABY for YELP
CDLADVANCEBLOCK for YELP
CDLBELTHOLD for YELP
CDLBREAKAWAY for YELP
CDLCLOSINGMARUBOZU for YELP
CDLCONCEALBABYSWALL for YELP
CDLCOUNTERATTACK for YELP
CDLDARKCLOUDCOVER for YELP
CDLDOJI for YELP
CDLDOJISTAR for YELP
CDLDRAGONFLYDOJI for YELP
CDLENGULFING for YELP
CDLEVENINGDOJISTAR for YELP
CDLEVENINGSTAR for YELP
CDLGAPSIDESIDEWHITE for YELP
CDLGRAVESTONEDOJI for YELP
CDLHAMMER for YELP
CDLHANGINGMAN for YELP
CDLHARAMI for YELP
CDLHARAMICROSS for YELP
CDLHIGHWAVE for YELP
CDLHIKKAKE for YELP
CDLHIKKAKEMOD for YELP
CDLHOMINGPIGEON for YELP
CDLIDENTICAL3CROWS for YELP
CDLINNECK for YELP
CDLINVERTEDHAMMER for YELP
CDLKICKING for YELP
CDLKICKINGBYLENGTH for YELP
CDLLADDERBOTTOM for YELP
CDLLONGLEGGEDDOJI for YELP
CDLLONGLINE for YELP
CDLMARUBOZU for YELP
CDLMATCHINGLOW for YELP
CDLMATHOLD for YELP
CDLMORN

CDLSTICKSANDWICH for YORW
CDLTAKURI for YORW
CDLTASUKIGAP for YORW
CDLTHRUSTING for YORW
CDLTRISTAR for YORW
CDLUNIQUE3RIVER for YORW
CDLUPSIDEGAP2CROWS for YORW
CDLXSIDEGAP3METHODS for YORW
CDL2CROWS for YUM
CDL3BLACKCROWS for YUM
CDL3INSIDE for YUM
CDL3LINESTRIKE for YUM
CDL3OUTSIDE for YUM
CDL3STARSINSOUTH for YUM
CDL3WHITESOLDIERS for YUM
CDLABANDONEDBABY for YUM
CDLADVANCEBLOCK for YUM
CDLBELTHOLD for YUM
CDLBREAKAWAY for YUM
CDLCLOSINGMARUBOZU for YUM
CDLCONCEALBABYSWALL for YUM
CDLCOUNTERATTACK for YUM
CDLDARKCLOUDCOVER for YUM
CDLDOJI for YUM
CDLDOJISTAR for YUM
CDLDRAGONFLYDOJI for YUM
CDLENGULFING for YUM
CDLEVENINGDOJISTAR for YUM
CDLEVENINGSTAR for YUM
CDLGAPSIDESIDEWHITE for YUM
CDLGRAVESTONEDOJI for YUM
CDLHAMMER for YUM
CDLHANGINGMAN for YUM
CDLHARAMI for YUM
CDLHARAMICROSS for YUM
CDLHIGHWAVE for YUM
CDLHIKKAKE for YUM
CDLHIKKAKEMOD for YUM
CDLHOMINGPIGEON for YUM
CDLIDENTICAL3CROWS for YUM
CDLINNECK for YUM
CDLINVERTEDHAMMER for YUM
CDLKICKING for YUM
CDLKICKINGBYLENGT

CDL2CROWS for ZG
CDL3BLACKCROWS for ZG
CDL3INSIDE for ZG
CDL3LINESTRIKE for ZG
CDL3OUTSIDE for ZG
CDL3STARSINSOUTH for ZG
CDL3WHITESOLDIERS for ZG
CDLABANDONEDBABY for ZG
CDLADVANCEBLOCK for ZG
CDLBELTHOLD for ZG
CDLBREAKAWAY for ZG
CDLCLOSINGMARUBOZU for ZG
CDLCONCEALBABYSWALL for ZG
CDLCOUNTERATTACK for ZG
CDLDARKCLOUDCOVER for ZG
CDLDOJI for ZG
CDLDOJISTAR for ZG
CDLDRAGONFLYDOJI for ZG
CDLENGULFING for ZG
CDLEVENINGDOJISTAR for ZG
CDLEVENINGSTAR for ZG
CDLGAPSIDESIDEWHITE for ZG
CDLGRAVESTONEDOJI for ZG
CDLHAMMER for ZG
CDLHANGINGMAN for ZG
CDLHARAMI for ZG
CDLHARAMICROSS for ZG
CDLHIGHWAVE for ZG
CDLHIKKAKE for ZG
CDLHIKKAKEMOD for ZG
CDLHOMINGPIGEON for ZG
CDLIDENTICAL3CROWS for ZG
CDLINNECK for ZG
CDLINVERTEDHAMMER for ZG
CDLKICKING for ZG
CDLKICKINGBYLENGTH for ZG
CDLLADDERBOTTOM for ZG
CDLLONGLEGGEDDOJI for ZG
CDLLONGLINE for ZG
CDLMARUBOZU for ZG
CDLMATCHINGLOW for ZG
CDLMATHOLD for ZG
CDLMORNINGDOJISTAR for ZG
CDLMORNINGSTAR for ZG
CDLONNECK for ZG
CDLPIERCING for ZG
CDLRICK

CDL2CROWS for ZGNX
CDL3BLACKCROWS for ZGNX
CDL3INSIDE for ZGNX
CDL3LINESTRIKE for ZGNX
CDL3OUTSIDE for ZGNX
CDL3STARSINSOUTH for ZGNX
CDL3WHITESOLDIERS for ZGNX
CDLABANDONEDBABY for ZGNX
CDLADVANCEBLOCK for ZGNX
CDLBELTHOLD for ZGNX
CDLBREAKAWAY for ZGNX
CDLCLOSINGMARUBOZU for ZGNX
CDLCONCEALBABYSWALL for ZGNX
CDLCOUNTERATTACK for ZGNX
CDLDARKCLOUDCOVER for ZGNX
CDLDOJI for ZGNX
CDLDOJISTAR for ZGNX
CDLDRAGONFLYDOJI for ZGNX
CDLENGULFING for ZGNX
CDLEVENINGDOJISTAR for ZGNX
CDLEVENINGSTAR for ZGNX
CDLGAPSIDESIDEWHITE for ZGNX
CDLGRAVESTONEDOJI for ZGNX
CDLHAMMER for ZGNX
CDLHANGINGMAN for ZGNX
CDLHARAMI for ZGNX
CDLHARAMICROSS for ZGNX
CDLHIGHWAVE for ZGNX
CDLHIKKAKE for ZGNX
CDLHIKKAKEMOD for ZGNX
CDLHOMINGPIGEON for ZGNX
CDLIDENTICAL3CROWS for ZGNX
CDLINNECK for ZGNX
CDLINVERTEDHAMMER for ZGNX
CDLKICKING for ZGNX
CDLKICKINGBYLENGTH for ZGNX
CDLLADDERBOTTOM for ZGNX
CDLLONGLEGGEDDOJI for ZGNX
CDLLONGLINE for ZGNX
CDLMARUBOZU for ZGNX
CDLMATCHINGLOW for ZGNX
CDLMATHOLD for ZGNX
CDLMORN

CDLUPSIDEGAP2CROWS for ZUMZ
CDLXSIDEGAP3METHODS for ZUMZ
CDL2CROWS for ZUO
CDL3BLACKCROWS for ZUO
CDL3INSIDE for ZUO
CDL3LINESTRIKE for ZUO
CDL3OUTSIDE for ZUO
CDL3STARSINSOUTH for ZUO
CDL3WHITESOLDIERS for ZUO
CDLABANDONEDBABY for ZUO
CDLADVANCEBLOCK for ZUO
CDLBELTHOLD for ZUO
CDLBREAKAWAY for ZUO
CDLCLOSINGMARUBOZU for ZUO
CDLCONCEALBABYSWALL for ZUO
CDLCOUNTERATTACK for ZUO
CDLDARKCLOUDCOVER for ZUO
CDLDOJI for ZUO
CDLDOJISTAR for ZUO
CDLDRAGONFLYDOJI for ZUO
CDLENGULFING for ZUO
CDLEVENINGDOJISTAR for ZUO
CDLEVENINGSTAR for ZUO
CDLGAPSIDESIDEWHITE for ZUO
CDLGRAVESTONEDOJI for ZUO
CDLHAMMER for ZUO
CDLHANGINGMAN for ZUO
CDLHARAMI for ZUO
CDLHARAMICROSS for ZUO
CDLHIGHWAVE for ZUO
CDLHIKKAKE for ZUO
CDLHIKKAKEMOD for ZUO
CDLHOMINGPIGEON for ZUO
CDLIDENTICAL3CROWS for ZUO
CDLINNECK for ZUO
CDLINVERTEDHAMMER for ZUO
CDLKICKING for ZUO
CDLKICKINGBYLENGTH for ZUO
CDLLADDERBOTTOM for ZUO
CDLLONGLEGGEDDOJI for ZUO
CDLLONGLINE for ZUO
CDLMARUBOZU for ZUO
CDLMATCHINGLOW for ZUO
CDLMATHOLD 

In [8]:
dictListForDataFrame = list()
for pattern in patternList:
    dictOfPatterns[pattern] = [i for i in dictOfPatterns[pattern] if i != None]
    negReturns = [i for i in dictOfPatterns[pattern] if i<0]
    dictListForDataFrame.append({
        'pattern' : str(pattern)[10:-23],
        'meanReturn' : np.mean(dictOfPatterns[pattern]),
        'medianReturn' : np.median(dictOfPatterns[pattern]),
        'sharpe' : (np.mean(dictOfPatterns[pattern])/np.std(dictOfPatterns[pattern]))*np.sqrt(252),
        'absSharpe' : (abs(np.mean(dictOfPatterns[pattern]))/np.std(dictOfPatterns[pattern]))*np.sqrt(252),
        'sortino' : (np.mean(dictOfPatterns[pattern])/np.std(negReturns))*np.sqrt(252),
        'absSortino' : (abs(np.mean(dictOfPatterns[pattern]))/np.std(negReturns))*np.sqrt(252),
        'noOfTrades' : len(dictOfPatterns[pattern]),
        'totalNoOfDays' : totalNoOfDays
    })

In [9]:
finalDF = pd.DataFrame(dictListForDataFrame).sort_values(by= 'absSortino', ascending=False, ignore_index=True)

In [10]:
print(finalDF.totalNoOfDays[0]/365,'years')

48872.44657534247 years


In [11]:
finalDF[finalDF['noOfTrades'] > finalDF.totalNoOfDays[0]/100]

pattern  meanReturn  medianReturn    sharpe  absSharpe  \
2        CDLHANGINGMAN    0.420730      0.083501  1.839069   1.839069   
3   CDLCLOSINGMARUBOZU   -0.465463     -0.092910 -1.762535   1.762535   
5          CDLMARUBOZU   -0.513452      0.000000 -1.792513   1.792513   
7          CDLLONGLINE   -0.263176     -0.024629 -1.074876   1.074876   
19         CDLDOJISTAR    0.144130      0.000000  0.644916   0.644916   
20         CDLBELTHOLD   -0.177067      0.000000 -0.689287   0.689287   
23        CDLENGULFING   -0.139211     -0.055622 -0.584219   0.584219   
24         CDL3OUTSIDE   -0.139257     -0.078094 -0.580568   0.580568   
30        CDLSHORTLINE   -0.036363      0.000000 -0.168803   0.168803   
32          CDLHIKKAKE   -0.026552      0.000000 -0.128772   0.128772   
35           CDLHARAMI   -0.017882      0.000000 -0.090324   0.090324   
37      CDLSPINNINGTOP   -0.010212      0.000000 -0.050906   0.050906   
38         CDLHIGHWAVE   -0.005971      0.000000 -0.029947   0.029947   

     sortino  absSortino  noOfTrades  totalNoOfDays  
2   2.199277    2.199277      443605       17838443  
3  -1.938215    1.938215     1302542       17838443  
5  -1.884958    1.884958      683799       17838443  
7  -1.233856    1.233856     1561079       17838443  
19  0.819327    0.819327      179719       17838443  
20 -0.771800    0.771800     1690050       17838443  
23 -0.717079    0.717079      571618       17838443  
24 -0.634679    0.634679      256191       17838443  
30 -0.193749    0.193749     1049099       17838443  
32 -0.152309    0.152309      658654       17838443  
35 -0.110564    0.110564      491516       17838443  
37 -0.064049    0.064049     1170658       17838443  
38 -0.037917    0.037917      651818       17838443